# 5(1). LGBM

### Imports

In [1]:
# for read data
import os
import numpy as np
import pandas as pd

# Model
from lightgbm import LGBMClassifier     

# tunning
import optuna
from bayes_opt import BayesianOptimization
from sklearn import model_selection

# Out of Fold
from sklearn.metrics import log_loss  
from sklearn.model_selection import StratifiedKFold

# for save
import joblib

### Read data

In [3]:
path = (os.path.abspath("./input"))

X_train = pd.read_csv(path +'/feature_train_imp_LGBM.csv', encoding='cp949')
X_test = pd.read_csv(path +'/feature_test_imp_LGBM.csv', encoding='cp949')
y_train = pd.read_csv(path +'/y_train.csv', encoding='cp949').group

In [4]:
train_ID, test_ID = X_train.custid, X_test.custid
del X_train['custid'], X_test['custid']

## ▶ Hyperparameter Tuning
$~~~~$ [Tuning Guide] https://nurilee.com/2020/04/03/lightgbm-definition-parameter-tuning/

### $~~~~$ Obtuna

In [5]:
SKF = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 0)

In [ ]:
# Optuna
def objective(trial):
    lgbm_learning_rate = trial.suggest_float("learning_rate", 0.02, 0.05)
    lgbm_n_estimators = trial.suggest_int("n_estimators", 10, 1500)
    lgbm_max_depth = trial.suggest_int("max_depth", 20, 50)
    lgbm_num_leaves = trial.suggest_int("num_leaves", 30, 100)
    lgbm_min_child_samples = trial.suggest_int("min_child_samples", 20, 50)

    classifier_obj = LGBMClassifier(learning_rate=lgbm_learning_rate,
                                    n_estimators=lgbm_n_estimators,
                                    max_depth = lgbm_max_depth, 
                                    num_leaves = lgbm_num_leaves,
                                    min_child_samples = lgbm_min_child_samples, 
                                    objective='multiclass', metrics='multi_logloss', 
                                    num_gpu=1, verbose=10, random_state=0)
    
    logloss = []
    for tr_idx, val_idx in SKF.split(X_train, y_train):
        tr_x, tr_y = X_train.iloc[tr_idx], y_train.iloc[tr_idx]
        val_x, val_y = X_train.iloc[val_idx], y_train.iloc[val_idx]
        score = log_loss(val_y, classifier_obj.fit(tr_x, tr_y).predict_proba(val_x))
        logloss.append(score)
    return np.mean(logloss)

study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=3000)
print(study.best_trial)

[I 2022-06-14 14:36:46,297] A new study created in memory with name: no-name-01d70f20-f6dd-4094-a6f1-3f513296811f


[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.831575
[LightGBM] [Debug] Dataset::GetMultiBinFromAllFeatures: sparse rate 0.064813
[LightGBM] [Debug] init for col-wise cost 0.003959 seconds, init for row-wise cost 0.057254 seconds
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.119981 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 315284
[LightGBM] [Info] Number of data points in the train set: 17269, number of used features: 1549
[LightGBM] [Info] Start training from score -1.110379
[LightGBM] [Info] Start training from score -1.558854
[LightGBM] [Info] Start training from score -2.172403
[LightGBM] [Info] Start training from score -2.683399
[LightGBM] [Info] Start training from score -3.101228
[LightGBM] [Info] Start training from score -2.179546
[LightGBM] [Info] Start training from score -2.826173
[LightGBM] [Info] Start training from score -2.802984
[LightGBM] [Deb

[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 12
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 10
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 12
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 9
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 9
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 12
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 15
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 10
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 15
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 10
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 12
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 16
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 12
[LightGBM] [

[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 13
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 12
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 12
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 10
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 10
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 12
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 13
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 12
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 13
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 10
[LightGBM]

[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 15
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 14
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 12
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 13
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 10
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 10
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 10
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 15
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 17
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 15
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 10
[LightGBM] [Debug] Trained a tree with leaves = 58 and depth = 11
[LightGBM]

...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 77 and depth = 21
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 21 and depth = 9
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 17 and depth = 8
[LightGBM] [Debug] Trained a tree with leaves = 81 and depth = 22
[LightGBM] [Debug] Trained a tree with leaves = 81 and depth = 28
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 51 and depth = 12
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 23 and depth = 8
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 23 and depth = 10
[LightGBM] [Warning] No f

[LightGBM] [Debug] Trained a tree with leaves = 81 and depth = 26
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 45 and depth = 13
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 22 and depth = 9
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 22 and depth = 10
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 61 and depth = 14
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 20 and depth = 7
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 20 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 81 and depth = 19
[LightGBM] [Debug] Train

[LightGBM] [Debug] Trained a tree with leaves = 81 and depth = 29
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 46 and depth = 11
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 20 and depth = 9
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 22 and depth = 9
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 66 and depth = 22
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 20 and depth = 8
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 16 and depth = 6
[LightGBM] [Debug] Trained a tree with leaves = 81 and depth = 27
[LightGBM] [Debug] Trained

[LightGBM] [Debug] Trained a tree with leaves = 81 and depth = 17
[LightGBM] [Debug] Trained a tree with leaves = 81 and depth = 37
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 24 and depth = 10
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 22 and depth = 8
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 22 and depth = 9
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 75 and depth = 15
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 15 and depth = 8
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 19 and depth = 7
[LightGBM] [Debug] Trained

[LightGBM] [Debug] Trained a tree with leaves = 81 and depth = 17
[LightGBM] [Debug] Trained a tree with leaves = 81 and depth = 24
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 35 and depth = 10
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 20 and depth = 7
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 20 and depth = 10
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 47 and depth = 13
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 22 and depth = 8
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 20 and depth = 8
[LightGBM] [Debug] Traine

In [ ]:
optuna.visualization.plot_param_importances(study)

In [ ]:
lgbm_optuna = study.best_params
lgbm_optuna

In [ ]:
# score: 1.5582731398180367
lgbm_obtuna = LGBMClassifier(**lgbm_optuna, objective='multiclass', metrics='multi_logloss', num_gpu=1, random_state=0)

### $~~~~$ Bayesian Optimization

In [ ]:
def lgbm_bayesian(learning_rate, n_estimators, max_depth, num_leaves, min_child_samples, min_child_weight, reg_lambda, reg_alpha):
    params = {'learning_rate':0.03,
              'n_estimators':int(round(n_estimators)),
              'max_depth':int(round(max_depth)),
              'num_leaves':int(round(num_leaves)),
              'min_child_samples': int(round(min_child_samples))}
    
    lgbm = LGBMClassifier(**params, objective='multiclass', metrics='multi_logloss', random_state=0) #  num_gpu=1,
    
    logloss = []
    for tr_idx, val_idx in SKF.split(X_train, y_train):
        tr_x, tr_y = X_train.iloc[tr_idx], y_train.iloc[tr_idx]
        val_x, val_y = X_train.iloc[val_idx], y_train.iloc[val_idx]
        score = log_loss(val_y, lgbm.fit(tr_x, tr_y).predict_proba(val_x))
        logloss.append(score)
    return np.mean(logloss)

In [ ]:
bayesian_params = {'n_estimators':(800, 1500),
                   'max_depth':(20, 50),
                   'num_leaves':(5, 20),
                   'min_child_samples':(18, 80)}

In [ ]:
lgbm_bay = BayesianOptimization(f=lgbm_bayesian, pbounds=bayesian_params, random_state=0)
lgbm_bay.maximize(init_points=5, n_iter=1000)

In [ ]:
# dictionary에 있는 target값을 모두 추출
target_list = []
for result in lgbm_bay.res:
    target = result['target']
    target_list.append(target)
print(target_list)
# 가장 큰 target 값을 가지는 순번(index)를 추출
print('maximum target index:', np.argmin(np.array(target_list)))

In [ ]:
# 가장 큰 target값을 가지는 index값을 기준으로 res에서 해당 parameter 추출. 
max_dict = lgbm_bay.res[np.argmin(np.array(target_list))]['params']
max_dict['max_depth'] = int(max_dict['max_depth'])
max_dict['min_child_samples'] = int(max_dict['min_child_samples'])
max_dict['n_estimators'] = int(max_dict['n_estimators'])
max_dict['num_leaves'] = int(max_dict['num_leaves'])
max_dict

In [ ]:
# score: 1.5545960092945523
lgbm_bayesian = LGBMClassifier(**max_dict, objective='multiclass', metrics='multi_logloss', 
                               gpu_use_dp=True, gpu_device_id=0, num_gpu=1, random_state=0)  

## ▶ Out of Fold

In [ ]:
# obtuna, bayesian tuning 중 best model 선택
model = lgbm_bayesian

In [62]:
lgbm_pred = np.zeros((X_test.shape[0], 8))
loss_list = []
for tr_idx, val_idx in SKF.split(X_train, y_train):
    tr_x, tr_y = X_train.iloc[tr_idx], y_train.iloc[tr_idx]
    val_x, val_y = X_train.iloc[val_idx], y_train.iloc[val_idx]
    
    model.fit(tr_x, tr_y)
    pred = model.predict_proba(val_x)
    loss = log_loss(val_y, pred)
    loss_list.append(loss)
    
    sub_pred = np.array(model.predict_proba(X_test)) / 5  # averaging
    lgbm_pred += sub_pred
print(f'{model.__class__.__name__}의 5fold 평균 Log Loss는 {np.mean(loss_list)}')

LGBMClassifier의 5fold 평균 Log Loss는 1.5544245015547722


## ▶ Deploy Model&Submission data

### $~~~$ Model

In [2]:
model_path = (os.path.abspath("./model"))

joblib.dump(model, model_path+'/LGBM.pkl')

### $~~~$ Submission data

In [63]:
pred = pd.DataFrame(lgbm_pred)
pred.columns = ['F20','F30','F40','F50','M20','M30','M40','M50']
submissions = pd.concat([pd.Series(test_ID, name="ID"), pred] ,axis=1)

In [64]:
sub_path = (os.path.abspath("./submission"))

fname = '/submission_LGBM.csv'
submissions.to_csv(sub_path+fname, index=False)
print("'{}' is ready to submit." .format(fname))

'/submission_LGBM_bayesian.csv' is ready to submit.
